# fbiPy - Prisoners in the US
----

## Dataset: FBI

In [6]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import time
from scipy.stats import linregress
import scipy.stats as st
from datetime import date
import json
# Import API key
from config import apikey
import ctypes  # An included library with Python install.
import datetime

In [4]:
year_list = [2017, 2018, 2019]
year = 2019
if year in year_list:
    print("Yes")
else:
    print("No")

Yes


In [7]:
def Mbox(title, text, style):
    return ctypes.windll.user32.MessageBoxW(0, text, title, style)

def append_dict_to_df(current_dict, current_index, current_df):
    single_df = pd.DataFrame(current_dict, index=[current_index])
    if current_df.empty:
        current_df = single_df.copy()
    else:
        current_df = current_df.append(single_df)        
    current_index += 1
    return current_df,current_index

def get_offender_data(crime_type,variable,agency, year_list):
    endpoint = f"api/nibrs/{crime_type}/offender/agencies/{agency}/{variable}"
    done = False
    max_attempts = 5
    current_attemp = 1
    wait_time = 5
    df = pd.DataFrame()
    # Build query URL
    query_url = f"{base_url}{endpoint}?api_key={apikey}"
    # Call API and get response
    while (not done) & (current_attemp <= max_attempts):
        try:
            response = requests.get(query_url)
            if response.status_code == 200:
                data_json = response.json()
                df_idx = 0
                data_list = data_json['data']
                if len(data_list)>0:
                    for data_item in range(len(data_list)):
                        data_dict = data_list[data_item]
                        if data_dict['data_year'] in year_list:
                            new_dict = {
                                "data_year": data_dict['data_year'],
                                'key': data_dict['key'],
                                'value': data_dict['value']
                            }
                            df,df_idx = append_dict_to_df(new_dict, df_idx, df)
            done = True
#             break
        except ConnectionAbortedError as err: 
            print(err)
            print(f"Attempt # {current_attemp} failed. Waiting {wait_time} seconds before next attempt.")
            time.sleep(wait_time)
            current_attemp =+ 1    
    return df

In [190]:
def build_scatter_plot(df, colx, coly, title, xlabel, ylabel, file):
    # Build a scatter plot
    plt.scatter(df[colx], df[coly], marker="o")
    # Incorporate the other graph properties
    plt.title(title)
    plt.ylabel(ylabel)
    plt.xlabel(xlabel)
    plt.grid(True)
    # Save the figure
    plt.savefig(file)
    # Show plot
    plt.show()
    
def build_linear_regression(df, colx, coly, title, xlabel, ylabel, file, le_x, le_y, r_x, r_y):
    # Perform a linear regression on coly vs. colx
    x_values = df[colx]
    y_values = df[coly]
    # Calculate the line equation using linear regression function
    (slope, intercept, rvalue, pvalue, stderr) = linregress(x_values, y_values)
    regress_values = x_values * slope + intercept
    line_eq = "y = " + str(round(slope,2)) + "x + " + str(round(intercept,2))
    # Plot original data using Scatter type
    plt.scatter(x_values,y_values, label='original data')
    # Plot fitted line using Line type
    plt.plot(x_values,regress_values,"r-", label='fitted line')
    # Add line equation to plot
    plt.annotate(line_eq,(le_x,le_y),fontsize=15,color="red")
    # Set title, xlabel, ylabel and legend
    plt.title(title)
    plt.xlabel(xlabel)
    plt.ylabel(ylabel)
    plt.legend()
    # Show r-squared value
    r2_latex = r'$r^2 = $'
    r2_value = f'{r2_latex}{round(rvalue**2,4)}'
    plt.annotate(r2_value,(r_x,r_y),fontsize=15,color="green")
    print(f"The r-value is: {rvalue}")
    # Save the figure
    plt.savefig(file)
    # Show plot
    plt.show()

In [12]:
# Config information.
base_url = "https://api.usa.gov/crime/fbi/sapi/"
format_type = "json"

In [78]:
# AGENCIES
endpoint = "api/agencies"

# Build query URL
query_url = f"{base_url}{endpoint}?api_key={apikey}"

# Call API and get response
response = requests.get(query_url)
data_json = response.json()
agencies_df = pd.DataFrame()
idx = 0
for state in data_json:
#     print(state)
    for agency in data_json[state]:
#         print(agency)
        agency_dict = data_json[state][agency]
        agencies_df,idx = append_dict_to_df(agency_dict, idx, agencies_df)

ori                                        agency_name  \
0      HI0010000   Hawaii Police Department County Sheriff's Office   
1      HI0050000     Maui Police Department County Sheriff's Office   
2      HI0020000                         Honolulu Police Department   
3      HI0040000    Kauai Police Department County Sheriff's Office   
4      DE0030500                          Milford Police Department   
...          ...                                                ...   
18663  TN0200000                    Decatur County Sheriff's Office   
18664  TN0070100                          Jellico Police Department   
18665  DCMPD0000                       Washington Police Department   
18666  DCMTP0000                               Metro Transit Police   
18667  DC0011300  DC Fire and Emergency Medical Services Arson I...   

      agency_type_name            state_name state_abbr       division_name  \
0               County                Hawaii         HI             Pacific   
1               County                Hawaii         HI             Pacific   
2                 City                Hawaii         HI             Pacific   
3               County                Hawaii         HI             Pacific   
4                 City              Delaware         DE      South Atlantic   
...                ...                   ...        ...                 ...   
18663           County             Tennessee         TN  East South Central   
18664             City             Tennessee         TN  East South Central   
18665             City  District of Columbia         DC      South Atlantic   
18666            Other  District of Columbia         DC      South Atlantic   
18667            Other  District of Columbia         DC      South Atlantic   

      region_name region_desc   county_name  nibrs latitude longitude  \
0            West   Region IV        HAWAII  False  19.7167  -155.087   
1            West   Region IV          MAUI  False  20.8873  -156.488   
2            West   Region IV      HONOLULU   True  21.3043  -157.851   
3            West   Region IV         KAUAI  False   22.012  -159.706   
4           South  Region III  KENT; SUSSEX   True  38.9161  -75.4216   
...           ...         ...           ...    ...      ...       ...   
18663       South  Region III       DECATUR   True  35.6034  -88.1074   
18664       South  Region III      CAMPBELL   True   36.587  -84.1301   
18665       South  Region III                False  38.8948  -77.0152   
18666       South  Region III                 True  38.8974  -77.0189   
18667       South  Region III                False  38.9041  -77.0172   

      nibrs_start_date  
0                 None  
1                 None  
2           01/01/2018  
3                 None  
4           01/01/2001  
...                ...  
18663       11/01/1997  
18664       06/01/1998  
18665             None  
18666       01/01/2000  
18667             None  

[18668 rows x 13 columns]

In [9]:
# Output File (CSV)
output_data_file = "output_data/agencies.csv"

# Export file as a CSV
agencies_df.to_csv(output_data_file, index=False, header=True)   
agencies_df

NameError: name 'agencies_df' is not defined

In [10]:
# Output File (CSV)
output_data_file = "output_data/agencies.csv"


# Read file and store in Pandas data frame
agencies_df = pd.read_csv(output_data_file)


agencies_df

ori                                        agency_name  \
0      HI0010000   Hawaii Police Department County Sheriff's Office   
1      HI0050000     Maui Police Department County Sheriff's Office   
2      HI0020000                         Honolulu Police Department   
3      HI0040000    Kauai Police Department County Sheriff's Office   
4      DE0030500                          Milford Police Department   
...          ...                                                ...   
18663  TN0200000                    Decatur County Sheriff's Office   
18664  TN0070100                          Jellico Police Department   
18665  DCMPD0000                       Washington Police Department   
18666  DCMTP0000                               Metro Transit Police   
18667  DC0011300  DC Fire and Emergency Medical Services Arson I...   

      agency_type_name            state_name state_abbr       division_name  \
0               County                Hawaii         HI             Pacific   
1               County                Hawaii         HI             Pacific   
2                 City                Hawaii         HI             Pacific   
3               County                Hawaii         HI             Pacific   
4                 City              Delaware         DE      South Atlantic   
...                ...                   ...        ...                 ...   
18663           County             Tennessee         TN  East South Central   
18664             City             Tennessee         TN  East South Central   
18665             City  District of Columbia         DC      South Atlantic   
18666            Other  District of Columbia         DC      South Atlantic   
18667            Other  District of Columbia         DC      South Atlantic   

      region_name region_desc   county_name  nibrs   latitude   longitude  \
0            West   Region IV        HAWAII  False  19.716698 -155.086880   
1            West   Region IV          MAUI  False  20.887321 -156.487630   
2            West   Region IV      HONOLULU   True  21.304317 -157.850770   
3            West   Region IV         KAUAI  False  22.012038 -159.705965   
4           South  Region III  KENT; SUSSEX   True  38.916120  -75.421610   
...           ...         ...           ...    ...        ...         ...   
18663       South  Region III       DECATUR   True  35.603422  -88.107384   
18664       South  Region III      CAMPBELL   True  36.586983  -84.130090   
18665       South  Region III           NaN  False  38.894764  -77.015205   
18666       South  Region III           NaN   True  38.897390  -77.018940   
18667       South  Region III           NaN  False  38.904103  -77.017229   

      nibrs_start_date  
0                  NaN  
1                  NaN  
2           01/01/2018  
3                  NaN  
4           01/01/2001  
...                ...  
18663       11/01/1997  
18664       06/01/1998  
18665              NaN  
18666       01/01/2000  
18667              NaN  

[18668 rows x 13 columns]

In [200]:
# TEST: single Agency
crime_type = "property-crime"
variable = "age"
year = 2019
current_agency = "HI0020000"
sub_df = get_offender_data(crime_type,variable,current_agency,year)
sub_df

value  data_year  month_num       key
1       2       2019          0       0-9
3     602       2019          0     10-19
5    1063       2019          0     20-29
7     932       2019          0     30-39
9     520       2019          0     40-49
11    355       2019          0     50-59
13    131       2019          0     60-69
15     23       2019          0     70-79
17      3       2019          0     80-89
19      0       2019          0  90-Older
21   5856       2019          0   Unknown

In [13]:
# Pull data for Variable: AGE and Year: 2019
start_time = datetime.datetime.now()
print(f'Process Start Time: {start_time}')
crime_type_list = ["property-crime", "violent-crime"]
variable = "age"
# year_list = [2015, 2016, 2017, 2018, 2019]
year_list = [2017]
agency_crimes_stat = pd.DataFrame()
idx = 0
total_agencies = len(agencies_df)
for index, row in agencies_df.iterrows():
    current_agency = row['ori']
    print(f"Agency {row['ori']} #{index+1}/{total_agencies}")
    for crime_type in crime_type_list:
        for year in year_list:
            sub_df = get_offender_data(crime_type,variable,current_agency,year)
            if len(sub_df)>0:
                print(f"          CrimeType: {crime_type}, Year: {year}, Processing Data")
                total_crimes = 0
                for i in range(len(sub_df)):
                    total_crimes += sub_df.iloc[i,0]
                print(f"                    Total crimes {total_crimes}, Year: {year}")
                my_dict = {
                    'year': year,
                    "crime_type": crime_type,
                    'agency': current_agency,
                    'agency_name': row['agency_name'],
                    'county': row['county_name'],
                    'state': row['state_abbr'],
                    'state_name': row['state_name'],
                    'latitude': row['latitude'],
                    'longitude': row['longitude'],
                    'age 0-9': sub_df.iloc[0,0],
                    'age 10-19': sub_df.iloc[1,0],
                    'age 20-29': sub_df.iloc[2,0],
                    'age 30-39': sub_df.iloc[3,0],
                    'age 40-49': sub_df.iloc[4,0],
                    'age 50-59': sub_df.iloc[5,0],
                    'age 60-69': sub_df.iloc[6,0],
                    'age 70-79': sub_df.iloc[7,0],
                    'age 80-89': sub_df.iloc[8,0],
                    'age 90-Older': sub_df.iloc[9,0],
                    'age Unknown': sub_df.iloc[10,0],
                    'total_crimes': total_crimes
                }
                agency_crimes_stat,idx = append_dict_to_df(my_dict, idx, agency_crimes_stat)
            else:
                print(f"          CrimeType: {crime_type}, Year: {year}, No Data")
# Output File (CSV)
output_data_file = "output_data/agency_crimes_stat.csv"
# Export file as a CSV
agency_crimes_stat.to_csv(output_data_file, index=False, header=True)
end_time = datetime.datetime.now()
print(f'Process End Time: {end_time}')
elapsed_time = end_time - start_time
print(f'Elapsed Time: {elapsed_time}')
# Show DataFrame
agency_crimes_stat

Process Start Time: 2021-02-11 19:15:54.425697
Agency HI0010000 #1/18668


KeyboardInterrupt: 

In [203]:
# # Output File (CSV)
# output_data_file = "output_data/agency_crimes_stat.csv"
# # Export file as a CSV
# agency_crimes_stat.to_csv(output_data_file, index=False, header=True)
# Show DataFrame
agency_crimes_stat

year      crime_type     agency                      agency_name  \
0      2017  property-crime  DE0030500        Milford Police Department   
1      2017   violent-crime  DE0030500        Milford Police Department   
2      2017  property-crime  DE0030300         Laurel Police Department   
3      2017   violent-crime  DE0030300         Laurel Police Department   
4      2017  property-crime  DE0011900               Dover Fire Marshal   
...     ...             ...        ...                              ...   
12080  2017   violent-crime  TN0200000  Decatur County Sheriff's Office   
12081  2017  property-crime  TN0070100        Jellico Police Department   
12082  2017   violent-crime  TN0070100        Jellico Police Department   
12083  2017  property-crime  DCMTP0000             Metro Transit Police   
12084  2017   violent-crime  DCMTP0000             Metro Transit Police   

             county state            state_name   latitude  longitude  \
0      KENT; SUSSEX    DE              Delaware  38.916120 -75.421610   
1      KENT; SUSSEX    DE              Delaware  38.916120 -75.421610   
2            SUSSEX    DE              Delaware  38.677511 -75.335495   
3            SUSSEX    DE              Delaware  38.677511 -75.335495   
4              KENT    DE              Delaware        NaN        NaN   
...             ...   ...                   ...        ...        ...   
12080       DECATUR    TN             Tennessee  35.603422 -88.107384   
12081      CAMPBELL    TN             Tennessee  36.586983 -84.130090   
12082      CAMPBELL    TN             Tennessee  36.586983 -84.130090   
12083                  DC  District of Columbia  38.897390 -77.018940   
12084                  DC  District of Columbia  38.897390 -77.018940   

       age 0-9  ...  age 20-29  age 30-39  age 40-49  age 50-59  age 60-69  \
0            2  ...        151         89         67         47          6   
1            2  ...         30         14          4          3          0   
2            1  ...         58         24          9          5          1   
3            0  ...         22          9          4          1          0   
4            0  ...          0          0          0          0          0   
...        ...  ...        ...        ...        ...        ...        ...   
12080        0  ...          4          5          2          0          1   
12081        0  ...          6         30         11          1          0   
12082        0  ...          0          3          1          0          1   
12083        2  ...        104         40         17         20          2   
12084        0  ...        158         23         14         12          2   

       age 70-79  age 80-89  age 90-Older  age Unknown  total_crimes  
0              2          0             0          113           550  
1              0          0             0           20           105  
2              3          1             0           42           171  
3              0          0             0            6            66  
4              0          0             0            0             1  
...          ...        ...           ...          ...           ...  
12080          0          0             0            1            15  
12081          0          0             0           17            70  
12082          0          0             0            0             5  
12083          0          0             0          201           720  
12084          0          0             0          100           934  

[12085 rows x 21 columns]

In [ ]:
# Pull all data
start_time = datetime.datetime.now()
print(f'Process Start Time: {start_time}')
# crime_type_list = ["aggravated-assault", "burglary", "larceny", "motor-vehicle-theft",
#                    "homicide", "rape", "robbery", "arson", "property-crime", "violent-crime"]
crime_type_list = ["property-crime", "violent-crime"]
# variable_list = ["age", "count", "ethnicity", "race", "sex"]
variable_list = ["age", "sex"]
year_list = [2017, 2018, 2019]
# year_list = [2017]
agency_crimes = pd.DataFrame()
idx = 0
total_agencies = len(agencies_df)
for index, row in agencies_df.iterrows():
    current_agency = row['ori']
    print(f"Agency {current_agency} #{index+1}/{total_agencies}")
    for crime_type in crime_type_list:
        for variable in variable_list:
            template_dict = {
                "crime_type": crime_type,
                'agency': current_agency,
                'agency_name': row['agency_name'],
                'county': row['county_name'],
                'state': row['state_abbr'],
                'state_name': row['state_name'],
                'latitude': row['latitude'],
                'longitude': row['longitude']
            }
            sub_df = get_offender_data(crime_type,variable,current_agency,year_list)
            if len(sub_df)>0:
                print(f"          CrimeType: {crime_type}, Processing Data")
                for sub_index, sub_row in sub_df.iterrows():
                    current_dict = template_dict
                    current_dict.update({'key': sub_row['key']})
                    current_dict.update({'value': sub_row['value']})
                    current_dict.update({'year': sub_row['data_year']})
                    agency_crimes,idx = append_dict_to_df(current_dict, idx, agency_crimes)
            else:
                print(f"          CrimeType: {crime_type}, No Data")
    if ((index+1) % 10) == 0:
        percent = 100*(index+1)/total_agencies
        current_time = datetime.datetime.now()
        partial_time = current_time - start_time
        estimated_time_remaining = partial_time * ((100 / percent) - 1)
        percent = round(percent,2)
        print(f"Progress: {percent}% - Estimated time remaining: {estimated_time_remaining}")  
# Output File (CSV)
output_data_file = "output_data/agency_crimes.csv"
# Export file as a CSV
agency_crimes.to_csv(output_data_file, index=False, header=True)
end_time = datetime.datetime.now()
print(f'Process End Time: {end_time}')
elapsed_time = end_time - start_time
print(f'Elapsed Time: {elapsed_time}')
# Show DataFrame
agency_crimes

Process Start Time: 2021-02-11 21:40:50.292171
Agency HI0010000 #1/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.01% - Estimated remaining time: 6:51:57.428010
Agency HI0050000 #2/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.01% - Estimated remaining time: 14:17:24.825003
Agency HI0020000 #3/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.02% - Estimated remaining time: 12:06:16.218013
Agency HI0040000 #4/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          Crim

          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.16% - Estimated remaining time: 18:45:29.280624
Agency DE0010600 #30/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.16% - Estimated remaining time: 19:31:05.518752
Agency DE001500X #31/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.17% - Estimated remaining time: 18:47:43.593657
Agency DE0031600 #32/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime,

          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.31% - Estimated remaining time: 19:10:23.424265
Agency DE0031300 #58/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.31% - Estimated remaining time: 19:33:08.863081
Agency DE0012200 #59/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.32% - Estimated remaining time: 19:15:44.261312
Agency DE0010700 #60/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
    

          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.46% - Estimated remaining time: 18:52:13.236697
Agency TX1820000 #87/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.47% - Estimated remaining time: 18:39:08.653775
Agency TX1981000 #88/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.47% - Estimated remaining time: 18:48:09.716432
Agency TX1090300 #89/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          Crime

          CrimeType: violent-crime, No Data
Progress: 0.62% - Estimated remaining time: 17:48:59.049907
Agency TX0430500 #116/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.62% - Estimated remaining time: 18:01:19.430426
Agency TX0140000 #117/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 0.63% - Estimated remaining time: 17:50:35.133637
Agency TX2300300 #118/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 0.63% - Estimated remaining time: 17:58:36.051629
Agency TX0910400 #119/18668
      

...

          CrimeType: violent-crime, Processing Data
Progress: 64.66% - Estimated remaining time: 18:17:12.946014
Agency OH0314600 #12072/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.67% - Estimated remaining time: 18:17:00.600822
Agency OH0253400 #12073/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.67% - Estimated remaining time: 18:17:20.552789
Agency OH0230300 #12074/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.68% - Estimated remaining time: 

          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 64.82% - Estimated remaining time: 18:15:12.334792
Agency OH0130100 #12101/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.82% - Estimated remaining time: 18:15:31.050789
Agency OH0761100 #12102/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.83% - Estimated remaining time: 18:15:24.437766
Agency OH0480000 #12103/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: vi

          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.97% - Estimated remaining time: 18:15:36.988563
Agency OH0740600 #12129/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 64.97% - Estimated remaining time: 18:15:38.587289
Agency OH0520300 #12130/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 64.98% - Estimated remaining time: 18:15:34.073531
Agency OH0501800 #12131/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: vio

          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 65.12% - Estimated remaining time: 18:14:01.006413
Agency OH0480200 #12158/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 65.13% - Estimated remaining time: 18:13:54.355722
Agency OH0390500 #12159/18668
          CrimeType: property-crime, No Data
          CrimeType: property-crime, No Data
          CrimeType: violent-crime, No Data
          CrimeType: violent-crime, No Data
Progress: 65.13% - Estimated remaining time: 18:13:55.846483
Agency OH0281000 #12160/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: vi

          CrimeType: property-crime, No Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 65.27% - Estimated remaining time: 18:13:25.987305
Agency OH0660000 #12186/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 65.28% - Estimated remaining time: 18:13:21.455150
Agency OH0431200 #12187/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data
          CrimeType: violent-crime, Processing Data
Progress: 65.28% - Estimated remaining time: 18:13:44.158944
Agency OH0490200 #12188/18668
          CrimeType: property-crime, Processing Data
          CrimeType: property-crime, Processing Data
          CrimeType: violent-crime, Processing Data


In [ ]:
# Output File (CSV)
output_data_file = "output_data/agency_crimes.csv"
# Export file as a CSV
agency_crimes.to_csv(output_data_file, index=False, header=True)

# Show DataFrame
agency_crimes

## Plotting the Data


### x_values vs. y_values Plot

In [ ]:
# # build_scatter_plot(df, colx, coly, title, xlabel, ylabel, file)
# build_scatter_plot(agency_crimes_stat, county, total_crimes, "County vs Total crimes", "County", "Total crimes", 
#                    "output_data/county_total_crimes.png")

In [ ]:
# build_linear_plot(df, colx, coly, title, xlabel, ylabel, file)
# build_linear_plot(agency_crimes_stat, county, total_crimes, "County vs Total crimes", "County", "Total crimes", 
#                    "output_data/county_total_crimes.png")

## Linear Regression

In [ ]:
# build_linear_regression(df, colx, coly, title, xlabel, ylabel, file, le_x, le_y, r_x, r_y)